# Gradient Boosted Trees Baseline Advanced Optimization 

Cloned from: [Feature_selection_LR_airlinejoin (baseline-3)](tobe update)
- Has the hyperparameter tuning for the baseline with all features for midterm.

- What is this notebook for? 
  - Notebook that runs the baseline Random Forest with advanced optimization
  - Machine Learning Algorithms : Random Forest
  - Metrics: F1, accuracy, precision
  
---
  
- Data:
  - Final, cleaned weather
  - Cleaned flights minus (PR departure delay, PR arrival delay, carrier ordinal)

RF in spark

https://adb-731998097721284.4.azuredatabricks.net/?o=731998097721284#notebook/1898361324232092/command/1898361324232093

Feature selection in RF

https://antonhaugen.medium.com/feature-selection-for-pyspark-tree-classifiers-3be54a8bc493

# 0. Preparation

In [0]:
import pandas as pd
import numpy as np
import os
import matplotlib
import matplotlib.pyplot as plt
import seaborn as sns
import ast
from datetime import datetime, timedelta
from dateutil.relativedelta import relativedelta
import geopandas as gpd
import folium
import time
import hyperopt

from pyspark.sql.functions import col, max, min
from pyspark.sql.functions import col,isnan,when,count
from pyspark.sql.functions import desc
from pyspark.sql.types import DateType
from pyspark.ml.classification import LogisticRegression
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.feature import StandardScaler
from pyspark.ml.feature import MinMaxScaler
from pyspark.mllib.evaluation import MulticlassMetrics, BinaryClassificationMetrics
from pyspark.ml.evaluation import BinaryClassificationEvaluator
from pyspark.sql.functions import add_months, date_add
from pyspark.ml.classification import RandomForestClassifier
from sklearn.model_selection import RandomizedSearchCV
from pyspark.ml.classification import GBTClassifier


from hyperopt import tpe, hp, fmin, STATUS_OK
from hyperopt.pyll.base import scope

from datetime import datetime, timedelta
from dateutil.relativedelta import relativedelta
from hyperopt import Trials



In [0]:
# Put at the top of any notebooks for storing in blob

from pyspark.sql.functions import col, max

blob_container = "team06" # The name of your container created in https://portal.azure.com
storage_account = "apatel" # The name of your Storage account created in https://portal.azure.com
secret_scope = "team06" # The name of the scope created in your local computer using the Databricks CLI
secret_key = "team06" # The name of the secret key created in your local computer using the Databricks CLI 
blob_url = f"wasbs://{blob_container}@{storage_account}.blob.core.windows.net"
mount_path = "/mnt/mids-w261"

## Import fully joined data

In [0]:
# Added April 6 with new features
# df_5yr_join_april6 = spark.read.parquet(f'{blob_url}/full_join_mattsFeats_anandFeats_cleaned_extraFeatures_v4_4-6-22')

df_5yr_join_april7 = spark.read.parquet(f'{blob_url}/full_join_mattsFeats_anandFeats_cleaned_extraFeatures_upToOD_good_v8_4-6-22')

In [0]:
features_for_cv = ['DATE'] + outcomes_for_flights + feature_list_full_0
features_for_cv_april7 =  ['DATE'] + outcomes_for_flights + selected_features_match_XGboost

print(features_for_cv_april7)

['DATE', 'DEP_DEL15', 'DISTANCE', 'ORI_elevation', 'DEST_elevation', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'prior_arr_delayed', 'previous_ARR_DELAY_NEW', 'plane_is_here', 'avg_carrier_delay_24hrs', 'flights_sch_Today_ORIGIN', 'flights_sch_Today_DEST', 'avg_ori_airport_delay_24hrs', 'daytime', 'evening', 'new_england', 'mid_atlantic', 'south', 'midwest', 'southwest', 'west', 'pacific_islands', 'spring', 'winter', 'autumn', 'weekend_or_holiday', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'plane_is_here', 'previous_ARR_DELAY_NEW', 'avg_carrier_delay_24hrs', 'prior_arr_delayed', 'avg_ori_airport_delay_24hrs', 'depDelayPageRank', 'arrDelayPageRank', 'OC1_0_wind_gust_spd_rate_imp', 'AA1_1_liquid_precip', 'AA3_1_liquid_precip', 'gd1_0_sky_coverage', 'au2_4_extreme_wind_weather', 'mv1_0_sand_dust_near', 'mv1_0_thunder_rain_near', 'aw1_mw1_0_smoke_haze_dust', 'aw1_mw1_0_fog', 'aw1_mw1_0_rain_drizzle', 'aw1_mw1_0_freezing_rain_drizzle', 'aw1_mw1_0_snow', 'aw1_mw1_0_hail_or_ice', 'aw1_mw1_0_thunderstorm', 'aw1_mw1_0_tornado', 'SLP_0_avg_station_press_imp', 'WND_3_wind_speed_imp', 'CIG_0_sky_ceiling_height_imp', 'VIS_0_visibility_dist_imp', 'TMP_0_air_temperature_imp', 'DEW_0_dew_pt_temp_imp', 'MA1_0_altimeter_set_rate_imp', 'MA1_2_station_pres_rate_imp', 'GD1_3_cloud_height_imp', 'avg_hourly_delay_24hr', 'avg_OD_dep_del15_24hr', 'avg_OD_delay_min_24hr', 'avg_OD_num_flights_24hr', 'depDelayPageRank_ordinal', 'arrDelayPageRank_ordinal', 'departed_for_current_aiport', 'time_inb_flight_min', 'avg_time_inb_flights_carrier_24hr', 'avg_time_inb_flights_origin_24hr', 'avg_time_inb_flights_dest_24hr', 'avg_ori_DEP_DELAY_NEW_24hr', 'airline_carrier_del', 'airline_carrier_del_min', 'avg_carrier_delay_over15_lastQ', 'airline_carrier_del_ordinal', 'airline_carrier_del_min_ordinal', 'origin_avg_DEP_DEL15', 'origin_avg_DEP_DELAY_NEW', 'avg_origin_delay_over15_lastQ', 'origin_del_ordinal', 'origin_del_min_ordinal', 'OD_avg_DEP_DEL15', 'OD_avg_DEP_DELAY_NEW', 'avg_OD_delay_over15_lastQ', 'OD_del_ordinal', 'OD_del_min_ordinal']

In [0]:
features_list =  selected_features_match_XGboost

In [0]:
display(df_5yr_join_april7)

In [0]:
# null check
def displayMissingInDF(flights_df, cols_to_check = None):
  # train0_null_check = train0.drop("CRS_DEP_DATETIME_UTC_END")
  if type(cols_to_check)==list:
    pass
  else:
    cols_to_check = flights_df.columns
  null_cnt_df = flights_df.select([count(when(col(c).contains('None') | \
                            col(c).contains('NULL') | \
                            (col(c) == '' ) | \
                            col(c).isNull() | \
                            isnan(c), c 
                           )).alias(c)
                    for c in cols_to_check])

  display(null_cnt_df)

#Anand GBT Manual Simplified

In [0]:
def rebalanceDF(trainingDF, desired_neg_to_pos_ratio):
  original_dep_del15_count_df = trainingDF.groupby('DEP_DEL15').count()
  positiveTrainCount = original_dep_del15_count_df.filter(original_dep_del15_count_df.DEP_DEL15 ==  1).select(['count']).head()[0]
  negativeTrainCount = original_dep_del15_count_df.filter(original_dep_del15_count_df.DEP_DEL15 ==  0).select(['count']).head()[0]

  # undersampling the negative cases
  negativeDF = trainingDF.filter(trainingDF['DEP_DEL15']==0).sample(False, positiveTrainCount/negativeTrainCount*desired_neg_to_pos_ratio, seed=12345)
  positiveDF = trainingDF.filter(trainingDF['DEP_DEL15']==1)
  new_trainDF = positiveDF.union(negativeDF).cache()
  return new_trainDF

In [0]:
df_imported = spark.read.parquet(f'{blob_url}/full_join_mattsFeats_anandFeats_cleaned_extraFeatures_upToOD_good_v8_4-6-22')

In [0]:
feature_list_full = ['DISTANCE', 'ORI_elevation', 'DEST_elevation', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'prior_arr_delayed', 'previous_ARR_DELAY_NEW', 'plane_is_here', 'avg_carrier_delay_24hrs', 'flights_sch_Today_ORIGIN', 'flights_sch_Today_DEST', 'avg_ori_airport_delay_24hrs', 'daytime', 'evening', 'new_england', 'mid_atlantic', 'south', 'midwest', 'southwest', 'west', 'pacific_islands', 'spring', 'winter', 'autumn', 'weekend_or_holiday', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'plane_is_here', 'previous_ARR_DELAY_NEW', 'avg_carrier_delay_24hrs', 'prior_arr_delayed', 'avg_ori_airport_delay_24hrs', 'depDelayPageRank', 'arrDelayPageRank', 'OC1_0_wind_gust_spd_rate_imp', 'AA1_1_liquid_precip', 'AA3_1_liquid_precip', 'gd1_0_sky_coverage', 'au2_4_extreme_wind_weather', 'mv1_0_sand_dust_near', 'mv1_0_thunder_rain_near', 'aw1_mw1_0_smoke_haze_dust', 'aw1_mw1_0_fog', 'aw1_mw1_0_rain_drizzle', 'aw1_mw1_0_freezing_rain_drizzle', 'aw1_mw1_0_snow', 'aw1_mw1_0_hail_or_ice', 'aw1_mw1_0_thunderstorm', 'aw1_mw1_0_tornado', 'SLP_0_avg_station_press_imp', 'WND_3_wind_speed_imp', 'CIG_0_sky_ceiling_height_imp', 'VIS_0_visibility_dist_imp', 'TMP_0_air_temperature_imp', 'DEW_0_dew_pt_temp_imp', 'MA1_0_altimeter_set_rate_imp', 'MA1_2_station_pres_rate_imp', 'GD1_3_cloud_height_imp', 'avg_hourly_delay_24hr', 'avg_OD_dep_del15_24hr', 'avg_OD_delay_min_24hr', 'avg_OD_num_flights_24hr', 'depDelayPageRank_ordinal', 'arrDelayPageRank_ordinal', 'departed_for_current_aiport', 'time_inb_flight_min', 'avg_time_inb_flights_carrier_24hr', 'avg_time_inb_flights_origin_24hr', 'avg_time_inb_flights_dest_24hr', 'avg_ori_DEP_DELAY_NEW_24hr', 'airline_carrier_del', 'airline_carrier_del_min', 'avg_carrier_delay_over15_lastQ', 'airline_carrier_del_ordinal', 'airline_carrier_del_min_ordinal', 'origin_avg_DEP_DEL15', 'origin_avg_DEP_DELAY_NEW', 'avg_origin_delay_over15_lastQ', 'origin_del_ordinal', 'origin_del_min_ordinal', 'OD_avg_DEP_DEL15', 'OD_avg_DEP_DELAY_NEW', 'avg_OD_delay_over15_lastQ', 'OD_del_ordinal', 'OD_del_min_ordinal']

References

https://www.analyticsvidhya.com/blog/2016/02/complete-guide-parameter-tuning-gradient-boosting-gbm-python/

https://spark.apache.org/docs/latest/api/python/reference/api/pyspark.ml.classification.GBTClassifier.html

https://towardsdatascience.com/why-do-random-forest-and-gradient-boosted-decision-trees-have-vastly-different-optimal-max-depth-a64c2f63e127#:~:text=Shallow%20trees%20can%20only%20capture,low%20bias%20and%20high%20variance
> However, those of us who have experience with Random Forest might find it surprising that Random Forest and GBDT have vastly different optimal hyperparameters, even though both are collections of Decision Trees. In particular, they differ hugely in max_depth which is one of the most important hyperparameters. Random Forest usually have max_depth ≥ 15, while for GBDT it is typically 4 ≤ max_depth ≤ 8. In this article we will look into the cause for this discrepancy.

In [0]:
desired_neg_to_pos_ratio = 1.6

maxDepth=5
maxBins=64
minInstancesPerNode=10
maxIter=100
seed=12345
# stepSize=0.1
# lossType = 'logistic'
# featureSubsetStrategy='all'

CV_name = 'fold_1'
train_data = df_imported.where((col('YEAR').cast('int') == 2015))
holdout_data = df_imported.where((col('YEAR').cast('int') == 2019))
save_name = 'GBT_test_preds_4_9_'+CV_name

new_trainDF = rebalanceDF(train_data, desired_neg_to_pos_ratio)
holdout = holdout_data

# Assemble features
assembler = VectorAssembler().setInputCols(feature_list_full).setOutputCol('features')
assmb_train = assembler.transform(new_trainDF)
assmb_holdout = assembler.transform(holdout)

# modeling
gbt = GBTClassifier(featuresCol = 'features', labelCol = 'DEP_DEL15',
                            maxDepth=maxDepth, maxBins=maxBins, minInstancesPerNode=minInstancesPerNode, maxIter=maxIter, seed=seed)
gbtModel1 = gbt.fit(assmb_train)
predictions_fold_1 = gbtModel1.transform(assmb_holdout)

In [0]:
display(predictions_fold_1)

YEAR QUARTER MONTH DAY_OF_MONTH DAY_OF_WEEK FL_DATE OP_UNIQUE_CARRIER OP_CARRIER_AIRLINE_ID TAIL_NUM OP_CARRIER_FL_NUM ORIGIN_AIRPORT_ID ORIGIN_AIRPORT_SEQ_ID ORIGIN ORIGIN_STATE_ABR ORIGIN_STATE_FIPS ORIGIN_STATE_NM DEST_AIRPORT_ID DEST_AIRPORT_SEQ_ID DEST DEST_STATE_ABR DEST_STATE_FIPS DEST_STATE_NM CRS_DEP_TIME DEP_TIME DEP_DELAY DEP_DELAY_NEW DEP_DEL15 DEP_DELAY_GROUP DEP_TIME_BLK CRS_ARR_TIME ARR_TIME ARR_DELAY ARR_DELAY_NEW ARR_DEL15 CANCELLED ACTUAL_ELAPSED_TIME DISTANCE DISTANCE_GROUP CARRIER_DELAY WEATHER_DELAY NAS_DELAY LATE_AIRCRAFT_DELAY ORI_IATA ORI_station_id ORI_station_lat ORI_station_lon ORI_airport_lat ORI_airport_lon ORI_elevation ORI_dist_airp_sta DEST_IATA DEST_station_id DEST_station_lat DEST_station_lon DEST_airport_lat DEST_airport_lon DEST_elevation DEST_dist_airp_sta CRS_DEP_HRS CRS_DEP_MINS CRS_DEP_TIME_STR CRS_DEP_DT_STR CRS_DEP_DATETIME iata_code ORI_timezone CRS_DEP_DATETIME_UTC CRS_DEP_DATETIME_UTC_END CRS_DEP_DATETIME_UTC_START STATION DATE LATITUDE LONGITUDE ELEVATION REPORT_TYPE DEST_timezone DEP_HRS DEP_MINS DEP_TIME_STR DEP_DT_STR DEP_DATETIME ARR_DATETIME_ACTUAL_UTC late_night daytime evening region_name new_england mid_atlantic south midwest southwest west pacific_islands atlantic_islands spring summer autumn winter dep_date weekend_or_holiday flightID ID previous_flight_delay_status previous_flight_dep_time time_between_departures_min valid_dep_delay prior_dep_delayed previous_DEP_DELAY_NEW_value previous_DEP_DELAY_NEW previous_flight_arrdelay_status previous_flight_arr_time time_between_arrival_and_end_min valid_arr_delay prior_arr_delayed previous_ARR_DELAY_NEW_value previous_ARR_DELAY_NEW prev_arrival_airport plane_is_here avg_carrier_delay_24hrs flights_sch_Today_ORIGIN flights_sch_Today_DEST avg_ori_airport_delay_24hrs year_quarter quarter_enum quarter_enum_prev month_seq_index wnd_2_wind_obs_type wnd_3_wind_sp_rate cig_0_height vis_0_distance slp_0_day_avg tmp_0_air_temp dew_0_point_temp ma1_0_altimeter_setting_rate ma1_2_station_pressure_rate gd1_3_sky_cover_height WND_3_wind_speed CIG_0_sky_ceiling_height VIS_0_visibility_dist SLP_0_avg_station_press TMP_0_air_temperature DEW_0_dew_pt_temp MA1_0_altimeter_set_rate MA1_2_station_pres_rate OC1_0_wind_gust_spd_rate_imp GD1_3_cloud_height AA1_1_liquid_precip AA3_1_liquid_precip gd1_0_sky_coverage au2_4_extreme_wind_weather mv1_0_sand_dust_near mv1_0_thunder_rain_near aw1_mw1_0_smoke_haze_dust aw1_mw1_0_fog aw1_mw1_0_rain_drizzle aw1_mw1_0_freezing_rain_drizzle aw1_mw1_0_snow aw1_mw1_0_hail_or_ice aw1_mw1_0_thunderstorm aw1_mw1_0_tornado SLP_0_avg_station_press_imp WND_3_wind_speed_imp CIG_0_sky_ceiling_height_imp VIS_0_visibility_dist_imp TMP_0_air_temperature_imp DEW_0_dew_pt_temp_imp MA1_0_altimeter_set_rate_imp MA1_2_station_pres_rate_imp GD1_3_cloud_height_imp depDelayPageRank arrDelayPageRank UniqueID hour hour_UTC avg_hourly_delay_24hr OD_Pair avg_OD_dep_del15_24hr avg_OD_delay_min_24hr avg_OD_num_flights_24hr depDelayPageRank_ordinal arrDelayPageRank_ordinal recent_dep_time recent_dep_dest time_between_currentDepTime_recentDepTime dep_flight_after_prediction recent_dep_flight_coming_here departed_for_current_aiport 1st_most_recent_dep_UTC 2nd_most_recent_dep_UTC 1st_most_recent_arr_UTC 2nd_most_recent_arr_UTC 3rd_most_recent_arr_UTC col1_time_inb_flight_min col2_time_inb_flight_min col3_time_inb_flight_min time_inb_flight_min avg_time_inb_flights_carrier_24hr avg_time_inb_flights_origin_24hr avg_time_inb_flights_dest_24hr avg_ori_DEP_DELAY_NEW_24hr airline_carrier_del airline_carrier_del_min avg_carrier_delay_over15_lastQ airline_carrier_del_ordinal airline_carrier_del_min_ordinal origin_avg_DEP_DEL15 origin_avg_DEP_DELAY_NEW avg_origin_delay_over15_lastQ origin_del_ordinal origin_del_min_ordinal OD_avg_DEP_DEL15 OD_avg_DEP_DELAY_NEW avg_OD_delay_over15_lastQ OD_del_ordinal OD_del_min_ordinal features rawPrediction probability prediction 2019 1 1 1 2 2019-01-01 MQ 20398 N259NN 3574 11624 1162402 EYW FL 12 Florida 11298 1129806 

In [0]:
feature_for_analysis = ['UniqueID','DEP_DEL15','probability','prediction','features']
gbt_test_preds_fold_1 = predictions_fold_1.select(feature_for_analysis).withColumnRenamed('DEP_DEL15', 'label')

In [0]:
results = gbt_test_preds_fold_1.select(['prediction', 'label'])
metrics = MulticlassMetrics(results.rdd)
# Summary stats
print("Accuracy = %s" % metrics.accuracy)
print("Recall = %s" % metrics.recall(label=1))
print("Precision = %s" % metrics.precision(1))
print("F1 measure = %s" % metrics.fMeasure(1.0,1.0))

Accuracy = 0.8351072868083622
Recall = 0.5180691079309409
Precision = 0.562884770385347
F1 measure = 0.5395479246823572

In [0]:
desired_neg_to_pos_ratio = 1.6

maxDepth=5
maxBins=64
minInstancesPerNode=10
maxIter=100
seed=12345
# stepSize=0.1
# lossType = 'logistic'
# featureSubsetStrategy='all'

CV_name = 'fold_2'
train_data = df_imported.where((col('YEAR').cast('int') == 2016))
holdout_data = df_imported.where((col('YEAR').cast('int') == 2019))
save_name = 'gbt_test_preds_4_9_'+CV_name

new_trainDF = rebalanceDF(train_data, desired_neg_to_pos_ratio)
holdout = holdout_data

# Assemble features
assembler = VectorAssembler().setInputCols(feature_list_full).setOutputCol('features')
assmb_train = assembler.transform(new_trainDF)
assmb_holdout = assembler.transform(holdout)

# modeling
gbt = GBTClassifier(featuresCol = 'features', labelCol = 'DEP_DEL15',
                            maxDepth=maxDepth, maxBins=maxBins, minInstancesPerNode=minInstancesPerNode, maxIter=maxIter, seed=seed)
gbtModel2 = gbt.fit(assmb_train)
predictions_fold_2 = gbtModel2.transform(assmb_holdout)

In [0]:
gbt_test_preds_fold_2 = predictions_fold_2.select(feature_for_analysis).withColumnRenamed('DEP_DEL15', 'label')

In [0]:
results = gbt_test_preds_fold_2.select(['prediction', 'label'])
metrics = MulticlassMetrics(results.rdd)
# Summary stats
print("Accuracy = %s" % metrics.accuracy)
print("Recall = %s" % metrics.recall(label=1))
print("Precision = %s" % metrics.precision(1))
print("F1 measure = %s" % metrics.fMeasure(1.0,1.0))

Accuracy = 0.8252959255618117
Recall = 0.5548737148304919
Precision = 0.5301652495420728
F1 measure = 0.5422381520788138

In [0]:
desired_neg_to_pos_ratio = 1.6

maxDepth=5
maxBins=64
minInstancesPerNode=10
maxIter=100
seed=12345
# stepSize=0.1
# lossType = 'logistic'
# featureSubsetStrategy='all'

CV_name = 'fold_3'
train_data = df_imported.where((col('YEAR').cast('int') == 2017))
holdout_data = df_imported.where((col('YEAR').cast('int') == 2019))
save_name = 'gbt_test_preds_4_9_'+CV_name

new_trainDF = rebalanceDF(train_data, desired_neg_to_pos_ratio)
holdout = holdout_data

# Assemble features
assembler = VectorAssembler().setInputCols(feature_list_full).setOutputCol('features')
assmb_train = assembler.transform(new_trainDF)
assmb_holdout = assembler.transform(holdout)

# modeling
gbt = GBTClassifier(featuresCol = 'features', labelCol = 'DEP_DEL15',
                            maxDepth=maxDepth, maxBins=maxBins, minInstancesPerNode=minInstancesPerNode, maxIter=maxIter, seed=seed)
gbtModel3 = gbt.fit(assmb_train)
predictions_fold_3 = gbtModel3.transform(assmb_holdout)

In [0]:
gbt_test_preds_fold_3 = predictions_fold_3.select(feature_for_analysis).withColumnRenamed('DEP_DEL15', 'label')

In [0]:
results = gbt_test_preds_fold_3.select(['prediction', 'label'])
metrics = MulticlassMetrics(results.rdd)
# Summary stats
print("Accuracy = %s" % metrics.accuracy)
print("Recall = %s" % metrics.recall(label=1))
print("Precision = %s" % metrics.precision(1))
print("F1 measure = %s" % metrics.fMeasure(1.0,1.0))

Accuracy = 0.8288998288663139
Recall = 0.5408454808554952
Precision = 0.5412662249224283
F1 measure = 0.5410557710926145

In [0]:
desired_neg_to_pos_ratio = 1.6

maxDepth=5
maxBins=64
minInstancesPerNode=10
maxIter=100
seed=12345
# stepSize=0.1
# lossType = 'logistic'
# featureSubsetStrategy='all'

CV_name = 'fold_4'
train_data = df_imported.where(((col('YEAR').cast('int') == 2017) & (col('MONTH').cast('int') > 6)) | ((col('YEAR').cast('int') == 2018) & (col('MONTH').cast('int') < 7)))
holdout_data = df_imported.where((col('YEAR').cast('int') == 2019))
save_name = 'gbt_test_preds_4_9_'+CV_name

new_trainDF = rebalanceDF(train_data, desired_neg_to_pos_ratio)
holdout = holdout_data

# Assemble features
assembler = VectorAssembler().setInputCols(feature_list_full).setOutputCol('features')
assmb_train = assembler.transform(new_trainDF)
assmb_holdout = assembler.transform(holdout)

# modeling
gbt = GBTClassifier(featuresCol = 'features', labelCol = 'DEP_DEL15',
                            maxDepth=maxDepth, maxBins=maxBins, minInstancesPerNode=minInstancesPerNode, maxIter=maxIter, seed=seed)
gbtModel4 = gbt.fit(assmb_train)
predictions_fold_4 = gbtModel4.transform(assmb_holdout)

In [0]:
gbt_test_preds_fold_4 = predictions_fold_4.select(feature_for_analysis).withColumnRenamed('DEP_DEL15', 'label')

In [0]:
results = gbt_test_preds_fold_4.select(['prediction', 'label'])
metrics = MulticlassMetrics(results.rdd)
# Summary stats
print("Accuracy = %s" % metrics.accuracy)
print("Recall = %s" % metrics.recall(label=1))
print("Precision = %s" % metrics.precision(1))
print("F1 measure = %s" % metrics.fMeasure(1.0,1.0))

Accuracy = 0.8290463020890226
Recall = 0.5452587498030781
Precision = 0.5413266954504068
F1 measure = 0.5432856081142575

In [0]:
desired_neg_to_pos_ratio = 1.6

maxDepth=5
maxBins=64
minInstancesPerNode=10
maxIter=100
seed=12345
# stepSize=0.1
# lossType = 'logistic'
# featureSubsetStrategy='all'

CV_name = 'fold_5'
train_data = df_imported.where(((col('YEAR').cast('int') == 2016) & (col('MONTH').cast('int') > 6)) | ((col('YEAR').cast('int') == 2017) & (col('MONTH').cast('int') < 7)))
holdout_data = df_imported.where((col('YEAR').cast('int') == 2019))
save_name = 'gbt_test_preds_4_9_'+CV_name

new_trainDF = rebalanceDF(train_data, desired_neg_to_pos_ratio)
holdout = holdout_data

# Assemble features
assembler = VectorAssembler().setInputCols(feature_list_full).setOutputCol('features')
assmb_train = assembler.transform(new_trainDF)
assmb_holdout = assembler.transform(holdout)

# modeling
gbt = GBTClassifier(featuresCol = 'features', labelCol = 'DEP_DEL15',
                            maxDepth=maxDepth, maxBins=maxBins, minInstancesPerNode=minInstancesPerNode, maxIter=maxIter, seed=seed)
gbtModel5 = gbt.fit(assmb_train)
predictions_fold_5 = gbtModel5.transform(assmb_holdout)

In [0]:
gbt_test_preds_fold_5 = predictions_fold_5.select(feature_for_analysis).withColumnRenamed('DEP_DEL15', 'label')

In [0]:
results = gbt_test_preds_fold_5.select(['prediction', 'label'])
metrics = MulticlassMetrics(results.rdd)
# Summary stats
print("Accuracy = %s" % metrics.accuracy)
print("Recall = %s" % metrics.recall(label=1))
print("Precision = %s" % metrics.precision(1))
print("F1 measure = %s" % metrics.fMeasure(1.0,1.0))

Accuracy = 0.8337597883282634
Recall = 0.5269533356162712
Precision = 0.5574004169910147
F1 measure = 0.5417494213508606

In [0]:
gbt_test_preds_fold_1.write.parquet(f"{blob_url}/GBT_2019pred_table_cvgroup1_0410_xgbm")
gbt_test_preds_fold_2.write.parquet(f"{blob_url}/GBT_2019pred_table_cvgroup2_0410_xgbm")
gbt_test_preds_fold_3.write.parquet(f"{blob_url}/GBT_2019pred_table_cvgroup3_0410_xgbm")
gbt_test_preds_fold_4.write.parquet(f"{blob_url}/GBT_2019pred_table_cvgroup4_0410_xgbm")
gbt_test_preds_fold_5.write.parquet(f"{blob_url}/GBT_2019pred_table_cvgroup5_0410_xgbm")

## Generate CV hold out predictions for each of the CV models - needed for Matt's thresholding

In [0]:
# CV splits for it
val_data_1 = df_imported.where((col('YEAR').cast('int') == 2016))

val_data_2 = df_imported.where((col('YEAR').cast('int') == 2017))

val_data_3 = df_imported.where((col('YEAR').cast('int') == 2018))

val_data_4 = df_imported.where(((col('YEAR').cast('int') == 2018) & (col('MONTH').cast('int') > 6)))

val_data_5 = df_imported.where(((col('YEAR').cast('int') == 2017) & (col('MONTH').cast('int') > 6)) | ((col('YEAR').cast('int') == 2018) & (col('MONTH').cast('int') < 7)))

In [0]:
# Assemble these and transform to make predictions
assmb_holdout_CV1 = assembler.transform(val_data_1)
val_predictions_fold_1 = gbtModel5.transform(assmb_holdout_CV1)

assmb_holdout_CV2 = assembler.transform(val_data_2)
val_predictions_fold_2 = gbtModel5.transform(assmb_holdout_CV2)

assmb_holdout_CV3 = assembler.transform(val_data_3)
val_predictions_fold_3 = gbtModel5.transform(assmb_holdout_CV3)

assmb_holdout_CV4 = assembler.transform(val_data_4)
val_predictions_fold_4 = gbtModel5.transform(assmb_holdout_CV4)

assmb_holdout_CV5 = assembler.transform(val_data_5)
val_predictions_fold_5 = gbtModel5.transform(assmb_holdout_CV5)


# change the DEP_DEL15 to label
gbt_CV_preds_fold_1 = val_predictions_fold_1.select(feature_for_analysis).withColumnRenamed('DEP_DEL15', 'label')
gbt_CV_preds_fold_2 = val_predictions_fold_2.select(feature_for_analysis).withColumnRenamed('DEP_DEL15', 'label')
gbt_CV_preds_fold_3 = val_predictions_fold_3.select(feature_for_analysis).withColumnRenamed('DEP_DEL15', 'label')
gbt_CV_preds_fold_4 = val_predictions_fold_4.select(feature_for_analysis).withColumnRenamed('DEP_DEL15', 'label')
gbt_CV_preds_fold_5 = val_predictions_fold_5.select(feature_for_analysis).withColumnRenamed('DEP_DEL15', 'label')

In [0]:
display(gbt_CV_preds_fold_1)

UniqueID label probability prediction features B6N595JBLGBFLL2016-07-022016-07-02 20:47:00 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.5022491024331444, 0.49775089756685564)) 0.0 Map(vectorType -> sparse, length -> 85, indices -> List(0, 1, 2, 8, 9, 10, 11, 12, 19, 24, 29, 31, 32, 33, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 62, 63, 65, 66, 67, 68, 69, 70, 71, 73, 74, 75, 76, 78, 79, 80, 81, 82, 83, 84), values -> List(2327.0, 60.0, 9.0, 0.52, 27.0, 202.0, 0.15, 1.0, 1.0, 1.0, 0.52, 0.15, 0.003500544675913835, 0.0027747531201398517, 10163.0, 31.0, 11524.85510428101, 16000.0, 211.0, 144.0, 10135.871569703622, 10150.0, 449.78504672897196, 0.241, 0.15, 9.029411764705882, 66.0, 82.0, 64.0, 431.78, 212.18, 330.3, 9.029411764705882, 0.2174832779656472, 14.362938906848212, 3.0, 2.0, 0.15740380878352117, 9.674698795180722, 78.0, 166.0, 1.0, 356.0, 1.0, 1.0, 1.0)) UAN14704JACIAH2016-07-032016-07-03 13:45:00 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.6340875941071279, 0.3659124058928721)) 0.0 Map(vectorType -> dense, length -> 85, values -> List(1265.0, 6451.0, 97.0, 1.0, 60.0, 1.0, 56.0, 1.0, 0.18, 18.0, 291.0, 0.05, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 1.0, 60.0, 1.0, 56.0, 0.18, 1.0, 0.05, 0.0026349144472628, 0.0025650351982225914, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 10164.16002896452, 0.0, 22000.0, 16093.0, 110.0, 30.0, 10213.0, 8050.0, 3658.0, 0.084, 0.05, 4.35, 0.0, 81.0, 87.0, 1.0, 610.0, 498.03, 406.35, 481.47, 4.35, 0.1799934090296294, 13.464977980167172, 0.0, 6.0, 4.0, 0.11722141823444283, 10.40520984081042, 0.0, 168.0, 141.0, 0.3333333333333333, 138.66666666666666, 1.0, 81.0, 2.0)) UAN54711JACIAH2016-07-052016-07-05 13:45:00 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7421436041453152, 0.2578563958546848)) 0.0 Map(vectorType -> sparse, length -> 85, indices -> List(0, 1, 2, 7, 8, 9, 10, 11, 12, 19, 24, 27, 29, 31, 32, 33, 49, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 73, 74, 75, 76, 78, 79, 80, 81, 82, 83, 84), values -> List(1265.0, 6451.0, 97.0, 1.0, 0.1, 18.0, 391.0, 0.29, 1.0, 1.0, 1.0, 1.0, 0.1, 0.29, 0.0026349144472628, 0.0025650351982225914, 10164.16002896452, 22000.0, 16093.0, 110.0, 30.0, 10186.0, 8027.0, 2896.0, 0.078, 0.29, 27.142857142857142, 81.0, 87.0, 1.0, 681.0, 696.44, 701.07, 697.89, 27.142857142857142, 0.1799934090296294, 13.464977980167172, 6.0, 4.0, 0.11722141823444283, 10.40520984081042, 168.0, 141.0, 0.3333333333333333, 138.66666666666666, 1.0, 81.0, 2.0)) UAN17753JACIAH2016-07-062016-07-06 13:45:00 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7807225292880074, 0.21927747071199255)) 0.0 Map(vectorType -> sparse, length -> 85, indices -> List(0, 1, 2, 7, 8, 9, 10, 11, 12, 19, 27, 29, 31, 32, 33, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 73, 74, 75, 76, 78, 79, 80, 81, 82, 83, 84), values -> List(1265.0, 6451.0, 97.0, 1.0, 0.17, 18.0, 392.0, 0.11, 1.0, 1.0, 1.0, 0.17, 0.11, 0.0026349144472628, 0.0025650351982225914, 10164.16002896452, 15.0, 3353.0, 16093.0, 80.0, 30.0, 10173.0, 8016.0, 2591.0, 0.11, 1.0, 81.0, 87.0, 1.0, 681.0, 978.39, 396.39, 438.94, 4.833333333333333, 0.1799934090296294, 13.464977980167172, 6.0, 4.0, 0.11722141823444283, 10.40520984081042, 168.0, 141.0, 0.3333333333333333, 138.66666666666666, 1.0, 81.0, 2.0)) UAN27722JACIAH2016-07-072016-07-07 13:45:00 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.819293366903372, 0.18070663309662804)) 0.0 Map(vectorType -> sparse, length -> 85, indices -> List(0, 1, 2, 4, 7, 8, 9, 10, 11, 12, 19, 26, 27, 29, 31, 32, 33, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 73, 74, 75, 76, 78, 79, 80, 81, 82, 83, 84), values -> List(1265.0, 6451.0, 97.0, 1.0, 1.0, 0.22, 17.0, 391.0, 0.22, 1.0, 1.0, 1.0, 1.0, 0.22, 0.22, 0.0026349144472628, 0.0025650351982225914, 10164.16002896452, 26.0, 22000.0, 16093

In [0]:
# Save out these 5 to blob
gbt_CV_preds_fold_1.write.parquet(f"{blob_url}/GBT_CVpred_table_cvgroup1_0410_xgbm")
gbt_CV_preds_fold_2.write.parquet(f"{blob_url}/GBT_CVpred_table_cvgroup2_0410_xgbm")
gbt_CV_preds_fold_3.write.parquet(f"{blob_url}/GBT_CVpred_table_cvgroup3_0410_xgbm")
gbt_CV_preds_fold_4.write.parquet(f"{blob_url}/GBT_CVpred_table_cvgroup4_0410_xgbm")
gbt_CV_preds_fold_5.write.parquet(f"{blob_url}/GBT_CVpred_table_cvgroup5_0410_xgbm")


## Run Custom CV model + New Features(Tier1+Tier2)

In [0]:
analysis_df_0_xgbm = RFwithPredictionDf(1, train0_custom_april7, holdout0_custom_april7, selected_features_match_XGboost, verbose=0, 
                                                rebalance_input_tup=(True, 1.6), maxDepth=8, maxBins=64, minInstancesPerNode=10, numTrees=100, seed=12345)

In [0]:
display(analysis_df_0_xgbm)

DATE label probability prediction features rawPrediction 2016-07-02T18:00:00.000+0000 1.0 Map(vectorType -> dense, length -> 2, values -> List(0.6164000087300551, 0.38359999126994504)) 0.0 Map(vectorType -> sparse, length -> 85, indices -> List(0, 1, 2, 8, 9, 10, 11, 12, 19, 24, 29, 31, 32, 33, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 62, 63, 65, 66, 67, 68, 69, 70, 71, 73, 74, 75, 76, 78, 79, 80, 81, 82, 83, 84), values -> List(2327.0, 60.0, 9.0, 0.52, 27.0, 202.0, 0.15, 1.0, 1.0, 1.0, 0.52, 0.15, 0.003500544675913835, 0.0027747531201398517, 10163.0, 31.0, 11524.85510428101, 16000.0, 211.0, 144.0, 10135.871569703622, 10150.0, 449.78504672897196, 0.241, 0.15, 9.029411764705882, 66.0, 82.0, 64.0, 431.78, 212.18, 330.3, 9.029411764705882, 0.2174832779656472, 14.362938906848212, 3.0, 2.0, 0.15740380878352117, 9.674698795180722, 78.0, 166.0, 1.0, 356.0, 1.0, 1.0, 1.0)) Map(vectorType -> dense, length -> 2, values -> List(61.640000873005505, 38.3599991269945)) 2016-07-03T11:35:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7891279998071481, 0.210872000192852)) 0.0 Map(vectorType -> dense, length -> 85, values -> List(1265.0, 6451.0, 97.0, 1.0, 60.0, 1.0, 56.0, 1.0, 0.18, 18.0, 291.0, 0.05, 1.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 1.0, 60.0, 1.0, 56.0, 0.18, 1.0, 0.05, 0.0026349144472628, 0.0025650351982225914, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 10164.16002896452, 0.0, 22000.0, 16093.0, 110.0, 30.0, 10213.0, 8050.0, 3658.0, 0.084, 0.05, 4.35, 0.0, 81.0, 87.0, 1.0, 610.0, 498.03, 406.35, 481.47, 4.35, 0.1799934090296294, 13.464977980167172, 0.0, 6.0, 4.0, 0.11722141823444283, 10.40520984081042, 0.0, 168.0, 141.0, 0.3333333333333333, 138.66666666666666, 1.0, 81.0, 2.0)) Map(vectorType -> dense, length -> 2, values -> List(78.91279998071481, 21.0872000192852)) 2016-07-05T11:35:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7638749519166679, 0.23612504808333212)) 0.0 Map(vectorType -> sparse, length -> 85, indices -> List(0, 1, 2, 7, 8, 9, 10, 11, 12, 19, 24, 27, 29, 31, 32, 33, 49, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 73, 74, 75, 76, 78, 79, 80, 81, 82, 83, 84), values -> List(1265.0, 6451.0, 97.0, 1.0, 0.1, 18.0, 391.0, 0.29, 1.0, 1.0, 1.0, 1.0, 0.1, 0.29, 0.0026349144472628, 0.0025650351982225914, 10164.16002896452, 22000.0, 16093.0, 110.0, 30.0, 10186.0, 8027.0, 2896.0, 0.078, 0.29, 27.142857142857142, 81.0, 87.0, 1.0, 681.0, 696.44, 701.07, 697.89, 27.142857142857142, 0.1799934090296294, 13.464977980167172, 6.0, 4.0, 0.11722141823444283, 10.40520984081042, 168.0, 141.0, 0.3333333333333333, 138.66666666666666, 1.0, 81.0, 2.0)) Map(vectorType -> dense, length -> 2, values -> List(76.38749519166677, 23.61250480833321)) 2016-07-06T11:35:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.8031860612321495, 0.19681393876785044)) 0.0 Map(vectorType -> sparse, length -> 85, indices -> List(0, 1, 2, 7, 8, 9, 10, 11, 12, 19, 27, 29, 31, 32, 33, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 73, 74, 75, 76, 78, 79, 80, 81, 82, 83, 84), values -> List(1265.0, 6451.0, 97.0, 1.0, 0.17, 18.0, 392.0, 0.11, 1.0, 1.0, 1.0, 0.17, 0.11, 0.0026349144472628, 0.0025650351982225914, 10164.16002896452, 15.0, 3353.0, 16093.0, 80.0, 30.0, 10173.0, 8016.0, 2591.0, 0.11, 1.0, 81.0, 87.0, 1.0, 681.0, 978.39, 396.39, 438.94, 4.833333333333333, 0.1799934090296294, 13.464977980167172, 6.0, 4.0, 0.11722141823444283, 10.40520984081042, 168.0, 141.0, 0.3333333333333333, 138.66666666666666, 1.0, 81.0, 2.0)) Map(vectorType -> dense, length -> 2, values -> List(80.31860612321495, 19.681393876785044)) 2016-07-07T11:35:00.000+0000 0.0 Map(vectorType -> dense, length -> 2, values -> List(0.7616392377235378, 0.23836076227646222)) 0.0 Map(vectorType -> sparse, length -> 85, indices -> List(0, 1, 2, 4, 7, 8, 9, 10, 11, 12, 19, 26, 27, 29, 31, 32, 33, 49, 50, 51,

In [0]:
analysis_df = analysis_df_0
search_space = [0.2]

# Based on the dataframe with prob_1 and prob_0, convert the spark df to pandas df with TP/TN/FP/FN, calculate f1 score and returns the df of the result
def f1_Eval(search_space, analysis_df):

  f1_by_threshold = [['index','threshold','f1_score']]
  best_f1_score = 0
  best_f1_index = 0
  best_threshold = 0

  analysis_df_th = analysis_df.withColumn("prob_0", extract_prob_0_udf(col("probability"))).withColumn("prob_1", extract_prob_1_udf(col("probability")))

  for idx, threshold in enumerate(search_space):
    #global f1_by_threshold, analysis_df_th, best_f1_score
    print(f'threshold:{threshold}')
    
    def pred_by_threshold(x): #x: prob_1
      global threshold
      print(f'threshold: {threshold}, x: {x}')
      try:
        if x >= threshold:
            print(int(1))
            return int(1)
        elif x < threshold:
            print(int(1))
            return int(0)
      except ValueError:
            return None
    pred_by_threshold_udf = udf(pred_by_threshold, IntegerType())

    # add column of prediction 
    analysis_df_th = analysis_df_th.withColumn(("pred_"+str(idx)), pred_by_threshold_udf(col("prob_1")))
    # add evaluation column     
    analysis_df_th = analysis_df_th.withColumn(("eval_"+str(idx)), udf_evalPred(('pred_'+str(idx)),'label'))
    display(analysis_df_th)

    # gain a result
    result = analysis_df_th.groupby([("eval_"+str(idx))]).count()
    pdf_result = result.toPandas()
    print(pdf_result)

    TPTNFPFN_list = [i for i in pdf_result["eval_"+str(idx)]]
    if "TP" in TPTNFPFN_list:
      TP = list(pdf_result[pdf_result["eval_"+str(idx)]=='TP']['count'])[0]
    elif "TP" not in TPTNFPFN_list:
      TP = 0
    if "TN" in TPTNFPFN_list:
      TN = list(pdf_result[pdf_result["eval_"+str(idx)]=='TN']['count'])[0]
    elif "TN" not in TPTNFPFN_list:
      TN = 0
    if "FP" in TPTNFPFN_list:
      FP = list(pdf_result[pdf_result["eval_"+str(idx)]=='FP']['count'])[0]
    elif "FP" not in TPTNFPFN_list:
      FP = 0
    if "FN" in TPTNFPFN_list:
      FN = list(pdf_result[pdf_result["eval_"+str(idx)]=='FN']['count'])[0]
    elif "FN" not in TPTNFPFN_list:
      FN = 0

    # count TP/FP/FN and return zero if denominator/numerator of f1 is zero
    if 2*TP+FN+FP == 0:
      f1_score = 0
    elif 2*TP+FN+FP != 0:
      f1_score = 2*TP/(2*TP+FN+FP)
    print(f1_score)

    f1_by_threshold += [[idx,threshold,f1_score]]
    print(f1_by_threshold)

    if f1_score > best_f1_score:
      best_f1_score = f1_score
      best_f1_index = idx
      best_threshold = threshold
    print(f'idx: {idx}, threshold: {threshold}, f1 score: {f1_score}, best_f1_index: {best_f1_index}, best_threshold: {best_threshold }, best f1 score: {best_f1_score}')

  return f1_by_threshold, analysis_df_th, best_f1_score, best_f1_index, best_threshold

In [0]:
f1_by_threshold, analysis_df_th, best_f1_score, best_f1_index, best_threshold = f1_Eval(search_space, analysis_df_0)

In [0]:
analysis_df_th = analysis_df.withColumn("prob_0", extract_prob_0_udf(col("probability"))).withColumn("prob_1", extract_prob_1_udf(col("probability")))

  for idx, threshold in enumerate(search_space):
    #global f1_by_threshold, analysis_df_th, best_f1_score
    print(f'threshold:{threshold}')
    
    def pred_by_threshold(x): #x: prob_1
      global threshold
      print(f'threshold: {threshold}, x: {x}')
      try:
        if x >= threshold:
            print(int(1))
            return int(1)
        elif x < threshold:
            print(int(1))
            return int(0)
      except ValueError:
            return None
    pred_by_threshold_udf = udf(pred_by_threshold, IntegerType())

    # add column of prediction 
    analysis_df_th = analysis_df_th.withColumn(("pred_"+str(idx)), pred_by_threshold_udf(col("prob_1")))
    # add evaluation column     
    analysis_df_th = analysis_df_th.withColumn(("eval_"+str(idx)), udf_evalPred(('pred_'+str(idx)),'label'))
    display(analysis_df_th)


In [0]:
print(f'f1_by_threshold: {f1_by_threshold}')
print(f'analysis_df_th: {analysis_df_th}')
print(f'best_f1_score: {best_f1_score}')
print(f'best_f1_index: {best_f1_index}')
print(f'best_threshold: {best_threshold}')

In [0]:
selected_features_match_XGboost = ['DISTANCE', 'ORI_elevation', 'DEST_elevation', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'prior_arr_delayed', 'previous_ARR_DELAY_NEW', 'plane_is_here', 'avg_carrier_delay_24hrs', 'flights_sch_Today_ORIGIN', 'flights_sch_Today_DEST', 'avg_ori_airport_delay_24hrs', 'daytime', 'evening', 'new_england', 'mid_atlantic', 'south', 'midwest', 'southwest', 'west', 'pacific_islands', 'spring', 'winter', 'autumn', 'weekend_or_holiday', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW', 'plane_is_here', 'previous_ARR_DELAY_NEW', 'avg_carrier_delay_24hrs', 'prior_arr_delayed', 'avg_ori_airport_delay_24hrs', 'depDelayPageRank', 'arrDelayPageRank', 'OC1_0_wind_gust_spd_rate_imp', 'AA1_1_liquid_precip', 'AA3_1_liquid_precip', 'gd1_0_sky_coverage', 'au2_4_extreme_wind_weather', 'mv1_0_sand_dust_near', 'mv1_0_thunder_rain_near', 'aw1_mw1_0_smoke_haze_dust', 'aw1_mw1_0_fog', 'aw1_mw1_0_rain_drizzle', 'aw1_mw1_0_freezing_rain_drizzle', 'aw1_mw1_0_snow', 'aw1_mw1_0_hail_or_ice', 'aw1_mw1_0_thunderstorm', 'aw1_mw1_0_tornado', 'SLP_0_avg_station_press_imp', 'WND_3_wind_speed_imp', 'CIG_0_sky_ceiling_height_imp', 'VIS_0_visibility_dist_imp', 'TMP_0_air_temperature_imp', 'DEW_0_dew_pt_temp_imp', 'MA1_0_altimeter_set_rate_imp', 'MA1_2_station_pres_rate_imp', 'GD1_3_cloud_height_imp', 'avg_hourly_delay_24hr', 'avg_OD_dep_del15_24hr', 'avg_OD_delay_min_24hr', 'avg_OD_num_flights_24hr', 'depDelayPageRank_ordinal', 'arrDelayPageRank_ordinal', 'departed_for_current_aiport', 'time_inb_flight_min', 'avg_time_inb_flights_carrier_24hr', 'avg_time_inb_flights_origin_24hr', 'avg_time_inb_flights_dest_24hr', 'avg_ori_DEP_DELAY_NEW_24hr', 'airline_carrier_del', 'airline_carrier_del_min', 'avg_carrier_delay_over15_lastQ', 'airline_carrier_del_ordinal', 'airline_carrier_del_min_ordinal', 'origin_avg_DEP_DEL15', 'origin_avg_DEP_DELAY_NEW', 'avg_origin_delay_over15_lastQ', 'origin_del_ordinal', 'origin_del_min_ordinal', 'OD_avg_DEP_DEL15', 'OD_avg_DEP_DELAY_NEW', 'avg_OD_delay_over15_lastQ', 'OD_del_ordinal', 'OD_del_min_ordinal']

In [0]:
analysis_df_1_xgbm = RFwithPredictionDf(2, train1_custom_april7, holdout1_custom_april7, selected_features_match_XGboost, verbose=0, 
                                                rebalance_input_tup=(True, 1.6), maxDepth=8, maxBins=64, minInstancesPerNode=10, numTrees=100, seed=12345)

In [0]:

display(analysis_df_1)

In [0]:
analysis_df_2_xgbm = RFwithPredictionDf(3, train2_custom_april7, holdout2_custom_april7, selected_features_match_XGboost, verbose=0, 
                                                rebalance_input_tup=(True, 1.6), maxDepth=8, maxBins=64, minInstancesPerNode=10, numTrees=100, seed=12345)

In [0]:
display(analysis_df_2)

In [0]:
analysis_df_3_xgbm = RFwithPredictionDf(4, train3_custom_april7, holdout3_custom_april7, selected_features_match_XGboost, verbose=0, 
                                                rebalance_input_tup=(True, 1.6), maxDepth=8, maxBins=64, minInstancesPerNode=10, numTrees=100, seed=12345)

In [0]:
display(analysis_df_3)

In [0]:
analysis_df_4_xgbm = RFwithPredictionDf(5, train4_custom_april7, holdout4_custom_april7, selected_features_match_XGboost, verbose=0, 
                                                rebalance_input_tup=(True, 1.6), maxDepth=8, maxBins=64, minInstancesPerNode=10, numTrees=100, seed=12345)

In [0]:
display(analysis_df_4)

In [0]:
analysis_df_0.write.parquet(f"{blob_url}/RF_pred_table_cvgroup1_0410_xgbm")
analysis_df_1.write.parquet(f"{blob_url}/RF_pred_table_cvgroup2_0410_xgbm")
analysis_df_2.write.parquet(f"{blob_url}/RF_pred_table_cvgroup3_0410_xgbm")
analysis_df_3.write.parquet(f"{blob_url}/RF_pred_table_cvgroup4_0410_xgbm")
analysis_df_4.write.parquet(f"{blob_url}/RF_pred_table_cvgroup5_0410_xgbm")

In [0]:
metrics_0 = MulticlassMetrics(analysis_df_0_xgbm.rdd)
f1_model0 = metrics_0.fMeasure(1.0,1.0)
metrics_1 = MulticlassMetrics(analysis_df_1.rdd)
f1_model1 = metrics_1.fMeasure(1.0,1.0)
metrics_2 = MulticlassMetrics(analysis_df_2.rdd)
f1_model2 = metrics_2.fMeasure(1.0,1.0)
metrics_3 = MulticlassMetrics(analysis_df_3.rdd)
f1_model3 = metrics_3.fMeasure(1.0,1.0)
# metrics_4 = MulticlassMetrics(analysis_df_4.rdd)
# f1_model4 = metrics_4.fMeasure(1.0,1.0)

--------------------------------------------------------------------------- 
 NameError Traceback (most recent call last)
 <command-1858507102413967> in <module> 
 ----> 1 metrics_0 = MulticlassMetrics ( analysis_df_0 . rdd ) 
 2 f1_model0 = metrics_0 . fMeasure ( 1.0 , 1.0 ) 
 3 metrics_1 = MulticlassMetrics ( analysis_df_1 . rdd ) 
 4 f1_model1 = metrics_1 . fMeasure ( 1.0 , 1.0 ) 
 5 metrics_2 = MulticlassMetrics ( analysis_df_2 . rdd ) 

 NameError : name 'analysis_df_0' is not defined

In [0]:
print(f'f1_model0: {f1_model0}')
print(f'f1_model1: {f1_model1}')
print(f'f1_model2: {f1_model2}')
print(f'f1_model3: {f1_model3}')
print(f'f1_model4: {f1_model4}')

### Check the collinearity of the Tier1 + Tier2 features

In [0]:
# selected features

# tier 1 (criteria of 1 > 0.005)
selected_features_tier1 = 

print(f'selected_features_tier1: {len(selected_features_tier1)}')
print(f'{selected_features_tier1}')

# tier 1 + 2 (criteria of 2 > 0.0001)
selected_features_tier1_2 = 

print(f'selected_features_tier1 & 2: {len(selected_features_tier1_2)}')
print(f'{selected_features_tier1_2}')

# original features
print(f'feature_list_full_0: {len(feature_list_full_0)}')
print(f'{feature_list_full_0}')

df_5yr_join_cv_april7

In [0]:
from pyspark.mllib.stat import Statistics
from pyspark.ml.stat import Correlation

selected_features_tier1_A = ['DEP_DEL15', 'prior_dep_delayed', 'previous_DEP_DELAY_NEW']#, 'prior_arr_delayed']#, 'previous_ARR_DELAY_NEW']        
selected_features_tier1_B = ['DEP_DEL15', 'plane_is_here', 'avg_carrier_delay_24hrs', 'avg_ori_airport_delay_24hrs','evening']
selected_features_tier1_C = ['DEP_DEL15', 'avg_hourly_delay_24hr', 'avg_OD_dep_del15_24hr', 'avg_OD_delay_min_24hr', 'time_inb_flight_min','avg_ori_DEP_DELAY_NEW_24hr']

corr_df = df_5yr_join_cv_april7.select(selected_features_tier1_A)
# corr_df_B = df_5yr_join_cv_april7.select(selected_features_tier1_B)

col_names = corr_df.columns
features = corr_df.rdd.map(lambda row:row[0:])
corr_mat = Statistics.corr(features, method='pearson')
corr_df = pd.DataFrame(corr_mat)
corr_df.index, corr_df.columns = col_names, col_names
corr_df

### Sample result: Simple run with 10 features as of April 5

# 5. Threshold optimization in RF

Reference: [Difference between raw prediction and probability](https://stackoverflow.com/questions/37903288/what-do-columns-rawprediction-and-probability-of-dataframe-mean-in-spark-mll)

In [0]:
print(len(train0_custom_april7.columns))
print(len(holdout0_custom_april7.columns))

# analysis_df_1
# analysis_df_2
# analysis_df_3
# analysis_df_4
# analysis_df_5

feature_list = selected_features_tier1_2
train = train0_custom_april7 # 20150101-20151231
holdout = holdout0_custom_april7 # 20160101-20161231
maxDepth=8
maxBins=64
minInstancesPerNode=10
numTrees=100
seed=12345
rebalance_input_tup=(True, 1.6)
verbose=0
CV_group=1

## 5-1. Define Function for Threhold Optimization

### Add Columns that contains P(class=0), P(class=1)

In [0]:
# display(analysis_df.withColumn('prob_0',col('probability')['values']))
from pyspark.sql.functions import udf, col
from pyspark.sql.types import FloatType, DoubleType, IntegerType, StringType

def extract_prob_0(x):
    try:
        return float(x[0])  # Your VectorUDT is of length 2
    except ValueError:
        return None
      
def extract_prob_1(x):
    try:
        return float(x[1])  # Your VectorUDT is of length 2
    except ValueError:
        return None

extract_prob_0_udf = udf(extract_prob_0, DoubleType())
extract_prob_1_udf = udf(extract_prob_1, DoubleType())

### Define function that apply chosen threshold to final modeling. Returns table of prediction

In [0]:
# function that creates the column with P(class=0) and P(class=1)

from pyspark.sql.functions import udf, col
from pyspark.sql.types import FloatType, DoubleType, IntegerType, StringType

def extract_prob_0(x):
    try:
        return float(x[0])  # Your VectorUDT is of length 2
    except ValueError:
        return None

extract_prob_0_udf = udf(extract_prob_0, DoubleType())
########################################################################################
def extract_prob_1(x):
    try:
        return float(x[1])  # Your VectorUDT is of length 2
    except ValueError:
        return None

extract_prob_1_udf = udf(extract_prob_1, DoubleType())
########################################################################################

In [0]:
# define functions that returns 1 or 0 based on the probability and threshold 
def pred_by_threshold(x): #x: prob_1
  global threshold
  try:
    if x >= threshold:
      return int(1)
    elif x < threshold:
      return int(0)
  except ValueError:
      return None
pred_by_threshold_udf = udf(pred_by_threshold, IntegerType())
########################################################################################

# define functions that returns TP/FP/FN/TN based on the prediction in each threshold 
def evalPred(pred, true):
  if pred == 1:
    if true == 1:
      return 'TP'
    elif true == 0:
      return 'FP'
  elif pred == 0:
    if true == 1:
      return 'FN'
    elif true == 0:
      return 'TN'
udf_evalPred = udf(lambda x,y:evalPred(x,y), StringType()) 

########################################################################################

# Based on the dataframe with prob_1 and prob_0, convert the spark df to pandas df with TP/TN/FP/FN, calculate f1 score and returns the df of the result
def f1Eval(idx, threshold):

  global f1_by_threshold, analysis_df_th, best_f1_score
  
  # add column of prediction 
  analysis_df_th = analysis_df_th.withColumn(("pred_"+str(idx)), pred_by_threshold_udf(col("prob_1")))
  # add evaluation column     
  analysis_df_th = analysis_df_th.withColumn(("eval_"+str(idx)), udf_evalPred(('pred_'+str(idx)),'label')) 
  
  # gain a result
  result = analysis_df_th.groupby([("eval_"+str(idx))]).count()
  pdf_result = result.toPandas()
  print(pdf_result)
  
  # count TP/FP/FN and return zero if denominator/numerator of f1 is zero
  if "TP" not in [i for i in pdf_result["eval_"+str(idx)]]:
    print('NO TP')
    f1_score = 0
  elif "FP" not in [i for i in pdf_result["eval_"+str(idx)]]:
    if "FN" not in [i for i in pdf_result["eval_"+str(idx)]]:
      FN, FP = 0, 0
      print('NO FN FP')
      TP = list(pdf_result[pdf_result["eval_"+str(idx)]=='TP']['count'])[0]
      f1_score = 2*TP/(2*TP+FN+FP)
    else:
      FN = list(pdf_result[pdf_result["eval_"+str(idx)]=='FN']['count'])[0]
      TP = list(pdf_result[pdf_result["eval_"+str(idx)]=='TP']['count'])[0]
      FP = 0
      print('NO FP')
      f1_score = 2*TP/(2*TP+FN+FP)
  elif "FN" not in [i for i in pdf_result["eval_"+str(idx)]]:
    FP = list(pdf_result[pdf_result["eval_"+str(idx)]=='FP']['count'])[0]
    TP = list(pdf_result[pdf_result["eval_"+str(idx)]=='TP']['count'])[0]
    FN = 0
    f1_score = 2*TP/(2*TP+FN+FP)
  else:
    FP = list(pdf_result[pdf_result["eval_"+str(idx)]=='FP']['count'])[0]
    TP = list(pdf_result[pdf_result["eval_"+str(idx)]=='TP']['count'])[0]
    FN = list(pdf_result[pdf_result["eval_"+str(idx)]=='FN']['count'])[0]      
    f1_score = 2*TP/(2*TP+FN+FP)
  
  f1_by_threshold += [[idx,threshold,f1_score]]
   
  if f1_score > best_f1_score:
    best_f1_score = f1_score
  print(f'idx: {idx}, threshold: {threshold}, f1 score: {f1_score}, best f1 score: {best_f1_score}')
  
  return f1_by_threshold, analysis_df_th
########################################################################################

In [0]:
#Add column
analysis_df_th = analysis_df_0.withColumn("prob_0", extract_prob_0_udf(col("probability")))\
                           .withColumn("prob_1", extract_prob_1_udf(col("probability")))

search_space = np.linspace(0.05, 0.95, 50)
f1_by_threshold = [['index','threshold','f1_score']]

best_f1_score = 0
best_f1_index = 0

for idx, threshold in enumerate(search_space):
  f1_by_threshold_0, analysis_df_th_0 = f1Eval(idx, threshold)

In [0]:
# Based on the dataframe with prob_1 and prob_0, convert the spark df to pandas df with TP/TN/FP/FN, calculate f1 score and returns the df of the result
def f1_Eval(search_space, analysis_df):

  f1_by_threshold = [['index','threshold','f1_score']]
  best_f1_score = 0
  best_f1_index = 0
  best_threshold = 0
  
  analysis_df_th = analysis_df.withColumn("prob_0", extract_prob_0_udf(col("probability"))).withColumn("prob_1", extract_prob_1_udf(col("probability")))
  
  for idx, threshold in enumerate(search_space):
    #global f1_by_threshold, analysis_df_th, best_f1_score
    
    # add column of prediction 
    analysis_df_th = analysis_df_th.withColumn(("pred_"+str(idx)), pred_by_threshold_udf(col("prob_1")))
    # add evaluation column     
    analysis_df_th = analysis_df_th.withColumn(("eval_"+str(idx)), udf_evalPred(('pred_'+str(idx)),'label')) 
    display(analysis_df_th)

    # gain a result
    result = analysis_df_th.groupby([("eval_"+str(idx))]).count()
    pdf_result = result.toPandas()
    print(pdf_result)

    TPTNFPFN_list = [i for i in pdf_result["eval_"+str(idx)]]
    if "TP" in TPTNFPFN_list:
      TP = list(pdf_result[pdf_result["eval_"+str(idx)]=='TP']['count'])[0]
    elif "TP" not in TPTNFPFN_list:
      TP = 0
    if "TN" in TPTNFPFN_list:
      TN = list(pdf_result[pdf_result["eval_"+str(idx)]=='TN']['count'])[0]
    elif "TN" not in TPTNFPFN_list:
      TN = 0
    if "FP" in TPTNFPFN_list:
      FP = list(pdf_result[pdf_result["eval_"+str(idx)]=='FP']['count'])[0]
    elif "FP" not in TPTNFPFN_list:
      FP = 0
    if "FN" in TPTNFPFN_list:
      FN = list(pdf_result[pdf_result["eval_"+str(idx)]=='FN']['count'])[0]
    elif "FN" not in TPTNFPFN_list:
      FN = 0

    # count TP/FP/FN and return zero if denominator/numerator of f1 is zero
    if 2*TP+FN+FP == 0:
      f1_score = 0
    elif 2*TP+FN+FP != 0:
      f1_score = 2*TP/(2*TP+FN+FP)

    f1_by_threshold += [[idx,threshold,f1_score]]

    if f1_score > best_f1_score:
      best_f1_score = f1_score
      best_f1_index = idx
      best_threshold = threshold
    print(f'idx: {idx}, threshold: {threshold}, f1 score: {f1_score}, best_f1_index: {best_f1_index}, best_threshold: {best_threshold }, best f1 score: {best_f1_score}')

  return f1_by_threshold, analysis_df_th, best_f1_score, best_f1_index, best_threshold

In [0]:
display(analysis_df_0)

In [0]:
search_space = np.linspace(0.05, 0.95, 50)
print(f'cv_group_0')
f1_by_threshold_0, analysis_df_th_0, best_f1_score, best_f1_index, best_threshold = f1_Eval(search_space, analysis_df_0)
f1_by_threshold_0

In [0]:
analysis_df_th_0

In [0]:
print(f'cv_group_1')
f1_by_threshold_1, analysis_df_th_1, best_f1_score, best_f1_index, best_threshold = f1_Eval(search_space, analysis_df_th_1)
print(f'cv_group_2')
f1_by_threshold_2, analysis_df_th_2, best_f1_score, best_f1_index, best_threshold = f1_Eval(search_space, analysis_df_th_2)
print(f'cv_group_3')
f1_by_threshold_3, analysis_df_th_3, best_f1_score, best_f1_index, best_threshold = f1_Eval(search_space, analysis_df_th_3)
print(f'cv_group_4')
f1_by_threshold_4, analysis_df_th_4, best_f1_score, best_f1_index, best_threshold  = f1_Eval(search_space, analysis_df_th_4)


In [0]:
CV_group_num = 1

def FinalTestWithBestThreshold(CV_group_num, trainAll, test, feature_list, threshold, maxDepth=5, maxBins=16, minInstancesPerNode=10, numTrees=100, seed=12345):
  # Assemble features
  assembler = VectorAssembler().setInputCols(feature_list)\
                            .setOutputCol('features')

  assmb_train = assembler.transform(trainAll)
  assmb_holdout = assembler.transform(test)

  # modeling
  rf = RandomForestClassifier(featuresCol = 'features', labelCol = 'DEP_DEL15',
                              maxDepth=maxDepth, maxBins=maxBins, minInstancesPerNode=minInstancesPerNode, numTrees=numTrees, seed=seed)
  rfModel = rf.fit(assmb_train)
  predictions = rfModel.transform(assmb_holdout)

  # predictions.select('DEP_DEL15','normalized_features')
  results = predictions.select(['prediction', 'DEP_DEL15'])
  results = results.withColumnRenamed('DEP_DEL15', 'label')
  # display(results.head(5))
  metrics = MulticlassMetrics(results.rdd)
  
  # gain prediction df and separate probability vector
  feature_for_analysis = ['DATE','DEP_DEL15','probability','prediction','features', 'rawPrediction']
  analysis_df = predictions.select(feature_for_analysis)
  
  extract_prob_0_udf = udf(extract_prob_0, DoubleType())
  extract_prob_1_udf = udf(extract_prob_1, DoubleType())
  analysis_df = analysis_df.withColumn("prob_0", extract_prob_0_udf(col("probability"))).withColumn("prob_1", extract_prob_1_udf(col("probability")))
  
  # based on the defined threshold, create vector of prediction
  # add column of prediction 
  analysis_df = analysis_df.withColumn(("pred_"+str(idx)), pred_by_threshold_udf(col("prob_1")))
  # add evaluation column     
  analysis_df = analysis_df.withColumn(("eval_"+str(idx)), udf_evalPred(('pred_'+str(idx)),'DEP_DEL15')) 
  
  # show prediction of the single model
  analysis_df_th = analysis_df
  f1_by_threshold = [['index','threshold','f1_score']]
  best_f1_score = 0
  best_f1_index = 0
  print(f'CV_group_num: {CV_group_num}#############################################################################')
  f1_by_threshold, analysis_df_th = f1Eval(CV_group_num, threshold)
  
  return analysis_df


In [0]:
analysis_df = FinalTestWithBestThreshold(CV_group_num, trainAll_april7, test_april7, feature_list, threshold=0.5, maxDepth=5, maxBins=16, minInstancesPerNode=10, numTrees=100, seed=12345)

### Quick hyperparameter tuning with 3years + 1years data work first optimization with all the five CV groups

## Write function that add column of predictions & evaluations of each threshold

In [0]:
search_space = np.linspace(0.05, 0.95, 50)
analysis_df_th = analysis_df_2

f1_by_threshold = [['index','threshold','f1_score']]
best_f1_score = 0
best_f1_index = 0

for idx, threshold in enumerate(search_space):
  
  # define functions that returns 1 or 0 based on the probability and threshold 
  def pred_by_threshold(x): #x: prob_1
    global threshold
    try:
      if x >= threshold:
        return int(1)
      elif x < threshold:
        return int(0)
    except ValueError:
        return None
  pred_by_threshold_udf = udf(pred_by_threshold, IntegerType())
  
  # add column of prediction 
  analysis_df_th = analysis_df_th.withColumn(("pred_"+str(idx)), pred_by_threshold_udf(col("prob_1")))
  
  # define functions that returns TP/FP/FN/TN based on the prediction in each threshold 
  def evalPred(pred, true):
    if pred == 1:
      if true == 1:
        return 'TP'
      elif true == 0:
        return 'FP'
    elif pred == 0:
      if true == 1:
        return 'FN'
      elif true == 0:
        return 'TN'

  # add evaluation column   
  udf_evalPred = udf(lambda x,y:evalPred(x,y), StringType()) 
  analysis_df_th = analysis_df_th.withColumn(("eval_"+str(idx)), udf_evalPred(('pred_'+str(idx)),'DEP_DEL15')) 
  
  # gain a result
  result = analysis_df_th.groupby([("eval_"+str(idx))]).count()
  pdf_result = result.toPandas()
  print(pdf_result)
  if "TP" not in [i for i in pdf_result["eval_"+str(idx)]]:
    print('NO TP')
    f1_score = 0
  elif "FP" not in [i for i in pdf_result["eval_"+str(idx)]]:
    if "FN" not in [i for i in pdf_result["eval_"+str(idx)]]:
      FN, FP = 0, 0
      print('NO FN FP')
      TP = list(pdf_result[pdf_result["eval_"+str(idx)]=='TP']['count'])[0]
      f1_score = 2*TP/(2*TP+FN+FP)
    else:
      FN = list(pdf_result[pdf_result["eval_"+str(idx)]=='FN']['count'])[0]
      TP = list(pdf_result[pdf_result["eval_"+str(idx)]=='TP']['count'])[0]
      FP = 0
      print('NO FP')
      f1_score = 2*TP/(2*TP+FN+FP)
  elif "FN" not in [i for i in pdf_result["eval_"+str(idx)]]:
    FP = list(pdf_result[pdf_result["eval_"+str(idx)]=='FP']['count'])[0]
    TP = list(pdf_result[pdf_result["eval_"+str(idx)]=='TP']['count'])[0]
    FN = 0
    f1_score = 2*TP/(2*TP+FN+FP)
  else:
    FP = list(pdf_result[pdf_result["eval_"+str(idx)]=='FP']['count'])[0]
    TP = list(pdf_result[pdf_result["eval_"+str(idx)]=='TP']['count'])[0]
    FN = list(pdf_result[pdf_result["eval_"+str(idx)]=='FN']['count'])[0]      
    f1_score = 2*TP/(2*TP+FN+FP)
  
  f1_by_threshold += [[idx,threshold,f1_score]]
   
  if f1_score > best_f1_score:
    best_f1_score = f1_score
    best_f1_index = idx
  print(f'idx: {idx}, threshold: {threshold}, f1 score: {f1_score}, best f1 index: {best_f1_index}, best f1 score: {best_f1_score}')

In [0]:
f1_by_threshold

## APPENDIX  Single run of random search with hyperopt

https://docs.databricks.com/_static/notebooks/hyperopt-spark-ml.html

https://docs.databricks.com/applications/machine-learning/automl-hyperparam-tuning/hyperopt-concepts.html